In [71]:
import pandas as pd
import os
import time
import openai
import pandas as pd
import warnings
import re

warnings.filterwarnings('ignore')

PATH_data_export = "/Users/huiziyu/Library/CloudStorage/GoogleDrive-huiziy@g.ucla.edu/My Drive/Project - LLM Bib in Biomedical & Health/data/processed"
df = pd.read_csv(f'{PATH_data_export}/relevant_data.csv')

In [62]:
def gpt_prompt(text):
    prompt = """You are a public health and AI researcher. 
    Please identify if the the following text is explicitly about utilizing language model (for example: GPT) in the healthcare and medical domain.
    The answer should be "Yes" or "No" or "Unknown"
    Output_format: "Enclose your output within <root></root> tags. 
    Present your reasoning in <reasoning></reasoning> tags and the final answer (Yes or No) in <final_answer></final_answer> tags, like <final_answer>{'Answer': 'Yes'}</final_answer>."
    The text is:
    """
    result = prompt+"\n"+text
    return result

In [63]:
from openai._client import OpenAI

SECRET_FILE = '../../secrets.txt'
with open('../../secrets.txt') as f:
    lines = f.readlines()
    for line in lines:
        if line.split(',')[0].strip() == "open_ai_key":
            open_ai_key = line.split(',')[1].strip()

openai_client = OpenAI(api_key=open_ai_key)

# GPT models (GPT-3.5 and GPT-4)
def run_gpt(text_prompt, max_tokens_to_sample: int = 3000, temperature: float = 0, client=openai_client, model = "gpt-3.5-turbo"):
    # use gpt-3.5-turbo unless specify gpt-4
    response = client.chat.completions.create(
      model = model, 
      messages=[
        {"role": "user", "content": text_prompt},
      ],
      temperature=temperature,
      max_tokens=max_tokens_to_sample
    )
    return response.choices[0].message.content

In [66]:
ID = 0
results_df = pd.DataFrame(columns=['ID', 'Original_Text', 'GPT_Results'])
for text in df.Title_abstract:
    print(text)
    text_prompt = gpt_prompt(text)
    if len(text_prompt) > 2000:
        text_prompt = text_prompt[:2000]
    result = run_gpt(text_prompt)
    results_df = results_df._append({'ID': ID, 'Original_Text': text, 'GPT_Results': result}, ignore_index=True)
    ID += 1
    print(result)

Performance of ChatGPT on USMLE: Potential for AI-assisted medical education using large language models. We evaluated the performance of a large language model called ChatGPT on the United States Medical Licensing Exam (USMLE), which consists of three exams: Step 1, Step 2CK, and Step 3. ChatGPT performed at or near the passing threshold for all three exams without any specialized training or reinforcement. Additionally, ChatGPT demonstrated a high level of concordance and insight in its explanations. These results suggest that large language models may have the potential to assist with medical education, and potentially, clinical decision-making.
<root>
<final_answer>{'Answer': 'Yes'}</final_answer>
<reasoning>The text explicitly mentions the use of a large language model called ChatGPT in the context of medical education and its performance on the United States Medical Licensing Exam (USMLE). It discusses how ChatGPT performed well on the exams and suggests that language models like

In [67]:
results_df.to_csv(f'{PATH_data_export}/gpt_results.csv', index=False)
results_df.to_excel(f'{PATH_data_export}/gpt_results.xlsx', index=False)

In [68]:
results_df

ID                                      Original_Text  \
0        0  Performance of ChatGPT on USMLE: Potential for...   
1        1  How Does ChatGPT Perform on the United States ...   
2        2  Performance of ChatGPT on USMLE: Potential for...   
3        3  ChatGPT Utility in Healthcare Education, Resea...   
4        4  ChatGPT and the rise of large language models:...   
...    ...                                                ...   
2667  2667  Influence on the accuracy in ChatGPT: Differen...   
2668  2668  Effect of Ramadan intermittent fasting on rena...   
2669  2669  Equity in Scientific Publishing: Can Artificia...   
2670  2670  Predicting seizure recurrence from medical rec...   
2671  2671  ChatGPT (Generated Pre-Trained Transformer) As...   

                                            GPT_Results  
0     <root>\n<final_answer>{'Answer': 'Yes'}</final...  
1     <root><final_answer>{'Answer': 'Yes'}</final_a...  
2     <root>\n<final_answer>{'Answer': 'Yes'}</final...  
3     <root>\n<final_answer>{'Answer': 'Yes'}</final...  
4     <root>\n<final_answer>{'Answer': 'Yes'}</final...  
...                                                 ...  
2667  <root>\n<final_answer>{'Answer': 'Yes'}</final...  
2668  <root><final_answer>{'Answer': 'No'}</final_an...  
2669  <root>\n<final_answer>{'Answer': 'No'}</final_...  
2670  <final_answer>{'Answer': 'Yes'}</final_answer>...  
2671  <root>\n<final_answer>{'Answer': 'Yes'}</final...  

[2672 rows x 3 columns]

In [72]:
## Parse the response from GPT
def extract_final_answer(df):
    """
    Extract the 'Yes' or 'No' answer from the <final_answer> tag in the GPT_Results column
    and assign it to a new column in the DataFrame.

    Parameters:
    df (pd.DataFrame): The DataFrame containing the GPT_Results.

    Returns:
    pd.DataFrame: The DataFrame with an additional column 'Extracted_Answer'.
    """
    # Define a regular expression pattern to find <final_answer>{'Answer': 'Yes/No'}</final_answer>
    pattern = r"<final_answer>\{'Answer': '(\w+)'\}</final_answer>"

    # Extract the value using the pattern
    df['Extracted_Answer'] = df['GPT_Results'].apply(lambda x: re.search(pattern, x).group(1) if re.search(pattern, x) else None)

    return df

results_clean = extract_final_answer(results_df)

In [74]:
results_clean.Extracted_Answer.value_counts()

Extracted_Answer
Yes        1447
No         1068
Unknown     128
Name: count, dtype: int64

In [78]:
results_no = results_clean[results_clean.Extracted_Answer == 'No']
results_no.to_csv(f'{PATH_data_export}/gpt_results_no.csv', index=False)
results_no.to_excel(f'{PATH_data_export}/gpt_results_no.xlsx', index=False)

results_yes = results_clean[results_clean.Extracted_Answer == 'Yes']
results_yes.to_csv(f'{PATH_data_export}/gpt_results_yes.csv', index=False)
results_yes.to_excel(f'{PATH_data_export}/gpt_results_yes.xlsx', index=False)

In [82]:
results_clean

ID                                      Original_Text  \
0        0  Performance of ChatGPT on USMLE: Potential for...   
1        1  How Does ChatGPT Perform on the United States ...   
2        2  Performance of ChatGPT on USMLE: Potential for...   
3        3  ChatGPT Utility in Healthcare Education, Resea...   
4        4  ChatGPT and the rise of large language models:...   
...    ...                                                ...   
2667  2667  Influence on the accuracy in ChatGPT: Differen...   
2668  2668  Effect of Ramadan intermittent fasting on rena...   
2669  2669  Equity in Scientific Publishing: Can Artificia...   
2670  2670  Predicting seizure recurrence from medical rec...   
2671  2671  ChatGPT (Generated Pre-Trained Transformer) As...   

                                            GPT_Results Extracted_Answer  
0     <root>\n<final_answer>{'Answer': 'Yes'}</final...              Yes  
1     <root><final_answer>{'Answer': 'Yes'}</final_a...              Yes  
2     <root>\n<final_answer>{'Answer': 'Yes'}</final...              Yes  
3     <root>\n<final_answer>{'Answer': 'Yes'}</final...              Yes  
4     <root>\n<final_answer>{'Answer': 'Yes'}</final...              Yes  
...                                                 ...              ...  
2667  <root>\n<final_answer>{'Answer': 'Yes'}</final...              Yes  
2668  <root><final_answer>{'Answer': 'No'}</final_an...               No  
2669  <root>\n<final_answer>{'Answer': 'No'}</final_...               No  
2670  <final_answer>{'Answer': 'Yes'}</final_answer>...              Yes  
2671  <root>\n<final_answer>{'Answer': 'Yes'}</final...              Yes  

[2672 rows x 4 columns]

In [83]:
df['ID'] = df.index
df = df.merge(results_clean, on='ID', how='left')

In [85]:
df.drop(columns=['Original_Text'], inplace=True)

In [87]:
df_relevant = df[df.Extracted_Answer == 'Yes']
df_relevant.to_csv(f'{PATH_data_export}/relevant_data_gpt.csv', index=False)
df_relevant.to_excel(f'{PATH_data_export}/relevant_data_gpt.xlsx', index=False)